__Računanje $H_\infty$ norme pomoću LNM__

In [1]:
import control as ct
import numpy as np
import scipy as sc

In [2]:
import pymor
import pymor.discretizations.iosys as iosys

In [3]:
from pymor.basic import *
from pymor.core.config import config
set_log_levels({'pymor.algorithms.gram_schmidt.gram_schmidt': 'WARNING'})

In [15]:
p = InstationaryProblem(
    StationaryProblem(
        domain=LineDomain([0.,1.], left='robin', right='robin'),
        diffusion=ConstantFunction(1., 1),
        robin_data=(ConstantFunction(1., 1), ExpressionFunction('(x[...,0] < 1e-10) * 1.', 1)),
        functionals={'output': ('l2_boundary', ExpressionFunction('(x[...,0] > (1 - 1e-10)) * 1.', 1))}
    ),
    ConstantFunction(0., 1),
    T=3.
)

d, _ = discretize_instationary_cg(p, diameter=1/50, nt=50)

00:39 DiffusionOperatorP1: Calulate gradients of shape functions transformed by reference map ...
00:39 DiffusionOperatorP1: Calculate all local scalar products beween gradients ...
00:39 DiffusionOperatorP1: Determine global dofs ...
00:39 DiffusionOperatorP1: Boundary treatment ...
00:39 DiffusionOperatorP1: Assemble system matrix ...
00:39 DiffusionOperatorP1: Calulate gradients of shape functions transformed by reference map ...
00:39 DiffusionOperatorP1: Calculate all local scalar products beween gradients ...
00:39 DiffusionOperatorP1: Determine global dofs ...
00:39 DiffusionOperatorP1: Boundary treatment ...
00:39 DiffusionOperatorP1: Assemble system matrix ...
00:39 L2ProductP1: Integrate the products of the shape functions on each element
00:39 L2ProductP1: Determine global dofs ...
00:39 L2ProductP1: Boundary treatment ...
00:39 L2ProductP1: Assemble system matrix ...
00:39 DiffusionOperatorP1: Calulate gradients of shape functions transformed by reference map ...
00:39 Diff

In [16]:
lti = d.to_lti()

In [17]:
from pymor.algorithms.to_matrix import to_matrix

In [18]:
A = to_matrix(lti.A,format='dense')
B = to_matrix(lti.B,format='dense')
C = to_matrix(lti.C,format='dense')
D = to_matrix(lti.D,format='dense')

In [26]:
%%time
lti.hinf_norm()

CPU times: user 418 µs, sys: 13 µs, total: 431 µs
Wall time: 452 µs


0.3333333333332594

In [20]:
import picos as pic
import cvxopt as cvx

In [21]:
AA = pic.new_param('AA',cvx.matrix(A))
BB = pic.new_param('BB',cvx.matrix(B))
CC = pic.new_param('CC',cvx.matrix(C))
DD = pic.new_param('DD',cvx.matrix(D))

In [22]:
n = np.size(AA)[0]

In [23]:
H = pic.Problem()
X = H.add_variable('X',(n,n),vtype='symmetric')
gamma = H.add_variable('gamma',1)
H.set_objective('min',gamma)
H.add_constraint(X>>0)
H.add_constraint( ((AA.T*X + X*AA & X*BB & CC.T) // (BB.T*X & -gamma & DD.T) // (CC & DD & -gamma )) << 0 )

<53×53 LMI Constraint: [AAᵀ·X + X·AA, X·BB, CCᵀ; BBᵀ·X, -gamma, DDᵀ; CC, DD, -gamma] ≼ 0>

In [27]:
%%time
H.solve(verbose = 0, solver = 'cvxopt');

CPU times: user 34.7 s, sys: 5.12 s, total: 39.8 s
Wall time: 10.8 s


{'cvxopt_sol': {'x': <1327x1 matrix, tc='d'>,
  'y': <0x1 matrix, tc='d'>,
  's': <5410x1 matrix, tc='d'>,
  'z': <5410x1 matrix, tc='d'>,
  'status': 'optimal',
  'gap': 8.928032640284613e-10,
  'relative gap': 2.6784097923146256e-09,
  'primal objective': 0.33333333329947223,
  'dual objective': 0.33333333330480375,
  'primal infeasibility': 1.265575137583725e-10,
  'dual infeasibility': 4.384820382091425e-09,
  'primal slack': 5.054705081915405e-13,
  'dual slack': 5.236947309112654e-13,
  'residual as primal infeasibility certificate': None,
  'residual as dual infeasibility certificate': None,
  'iterations': 19},
 'status': 'optimal',
 'time': 10.806421041488647,
 'primals': {'X': [0.31825297959015725,
   0.37502238667454174,
   0.27821577599148356,
   0.3100239882446223,
   0.3263285425172467,
   0.24897637608706874,
   0.2537184986779456,
   0.2680774308536679,
   0.29116473932122217,
   0.22812587567901035,
   0.204961540352629,
   0.21755212810969493,
   0.23815693630295615,


In [28]:
print ('Norma je {0:.8f}'.format(H.obj_value()))

Norma je 0.33333333
